# Model 9: Predict Star Formation Variables (sSFR, SFR, M*, age) Based on Visual Morphology (galaxy image)


In [1]:
#Loading needed modules and classes/functions 
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import torch
from torch.autograd import Variable
from torch.utils.data import DataLoader
from torch.utils.data import TensorDataset
from torchvision.datasets import ImageFolder 
from torchvision.io import read_image
from torchvision.io import decode_image
import torchvision
import torchvision.transforms as transforms
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import marvin
from marvin.tools.maps import Maps
from marvin.tools.image import Image
from marvin.utils.general.images import get_images_by_list
from marvin import config
from marvin.tools.cube import Cube
from sklearn import metrics
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.model_selection import train_test_split
import os
import shutil
from PIL import Image as image_PIL

#set config attributes and turn on global downloads of Marvin data
config.setRelease('DR15')
config.mode = 'local'
config.download = True



%matplotlib qt



[INFO]: No release version set. Setting default to DR15
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/redux/v2_4_3/drpall-v2_4_3.fits cannot be found. Setting drpall to None. (MarvinUserWarning)
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/analysis/v2_4_3/2.2.1/dapall-v2_4_3-2.2.1.fits cannot be found. Setting dapall to None. (MarvinUserWarning)
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/redux/v2_4_3/drpall-v2_4_3.fits cannot be found. Setting drpall to None. (MarvinUserWarning)
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/analysis/v2_4_3/2.2.1/dapall-v2_4_3-2.2.1.fits cannot be found. Setting dapall to None. (MarvinUserWarning)


# Importing Data from Schema Table

In [2]:


data=pd.read_csv('CompleteTable.csv')  #Importing All MaNGA Data from DPRall Schema

galaxy_list=np.loadtxt('Query Results',dtype=str) #Pulling Manga ID's of galaxies which satisfy log(M) > 9 and 0 < z < 0.1


#Problem with image associated with manga id at galaxy_list[3548], mangaid- 1-135668
galaxy_list=np.delete(galaxy_list,3548)

galaxy_list=np.unique(galaxy_list)


galaxy_index=np.zeros(len(galaxy_list)) 
for i in range (len(galaxy_list)): #Getting the index of these galaxies in the schema table
    galaxy_index[i]=np.where(data.loc[:,'mangaid']==galaxy_list[i])[0][0]

galaxy_index=np.array(galaxy_index,dtype=int) #Ensuring we have array that can be used to index, force int 

galaxies=data.iloc[galaxy_index] #DF of galaxies which satisfies the condition, contains all relevant schema data 

galaxies=galaxies.sort_values(by=['plateifu']) #Sorting galaxies by plateifu to match ImageFolder Output 

#Creating the arrays of the independent variables were are interested in, and dependent variable n 

mass=galaxies.loc[:,'nsa_sersic_mass']
log_mass=np.log10(mass)

SFR=galaxies.loc[:,'sfr_tot']
log_SFR=np.log10(SFR)

ha_flux=galaxies.loc[:,'emline_gflux_tot_ha_6564']

n=galaxies.loc[:,'nsa_sersic_n']
n=np.array(n,dtype=np.float32)
n=torch.from_numpy(n).to('cuda:0').reshape(-1,1)


# Importing Images from their Downloaded Locations 


In [3]:
# image_locations=[]
# for i in range (len(galaxy_list)):
#     image_locations.append(Image(galaxy_list[i]).filename)
    
# image_locations=np.array(image_locations,dtype=str)
# np.savetxt('Image Directories',image_locations,fmt='%s')

# image_locations=np.loadtxt('Image Directories',dtype=str)



In [4]:
# function to resize image
def resize_image(src_image, size=(128,128), bg_color="white"): 
    from PIL import Image, ImageOps 
    
    # resize the image so the longest dimension matches our target size
    src_image.thumbnail(size, Image.ANTIALIAS)
    
    # Create a new square background image
    new_image = Image.new("RGB", size, bg_color)
    
    # Paste the resized image into the center of the square background
    new_image.paste(src_image, (int((size[0] - src_image.size[0]) / 2), int((size[1] - src_image.size[1]) / 2)))
  
    # return the resized image
    return new_image




# Putting the Images into DataLoaders

In [5]:
# img_size=(128,128)

# image=ImageFolder('/home/juanp/sas/dr15/manga/spectro/redux/v2_4_3/') #Picks up 3590 pictures, directory list has lenght 3637 however 

# torch.manual_seed(15)
# np.random.seed(15)

image_directory='/home/juanp/Documents/Clean Images (Marvin Size Plateifu)'




batch_size=50
image_copies=11

def load_dataset(data_path):
    # Load all the images
    transformation = transforms.Compose([
        # Randomly augment the image data
            # Random horizontal flip
        transforms.RandomHorizontalFlip(0.5),
            # Random vertical flip
        transforms.RandomVerticalFlip(0.3),
        #Rotates the image by some angle
        transforms.RandomRotation(0,360),
        # transform to tensors
        transforms.ToTensor(),
        # Normalize the pixel values (in R, G, and B channels)
        # transforms.Normalize(mean=[0.5, 0.5, 0.5], std=[0.5, 0.5, 0.5])
    ])

    # Load all of the images, transforming them
    full_dataset = torchvision.datasets.ImageFolder(
        root=data_path,
        # transform=transformation
    )
    
    #This loop transforms the images and assigns them the correct label 

    full_dataset_v2 = []   
    for i in range(len(full_dataset)): 
        for j in range(image_copies):
            temp=transformation(resize_image(full_dataset[i][0]))
            full_dataset_v2.append((temp,log_mass.iloc[i])) 
    
    full_dataset=full_dataset_v2

    print(len(full_dataset))


    # Split into training (70% and testing (30%) datasets)
    train_size = int(0.7 * len(full_dataset))
    test_size = len(full_dataset) - train_size
    
    # use torch.utils.data.random_split for training/test split
    train_dataset, test_dataset = (full_dataset[0:train_size],full_dataset[train_size:train_size+test_size])
    
    # define a loader for the training data we can iterate through in 50-image batches
    train_loader = torch.utils.data.DataLoader(
        train_dataset,
        batch_size=batch_size,
        num_workers=0,
        shuffle=False
    )
    
    # define a loader for the testing data we can iterate through in 50-image batches
    test_loader = torch.utils.data.DataLoader(
        test_dataset,
        batch_size=batch_size,
        num_workers=0,
        shuffle=False
    )
        
    return train_loader, test_loader




#####################################################################################################



# Get the iterative dataloaders for test and training data
train_loader, test_loader = load_dataset(image_directory)
batch_size = train_loader.batch_size
print("Data loaders ready to read", image_directory)



39479
Data loaders ready to read /home/juanp/Documents/Clean Images (Marvin Size Plateifu)


In [6]:
# print(ImageFolder(image_directory))
# print(len(image_locations))
# # print(len(np.unique(image_locations)))
# print(len(np.unique(galaxy_list)))




# full_dataset = torchvision.datasets.ImageFolder(
#         root='/home/juanp/sas/dr15/manga/spectro/redux/v2_4_3/7968',
#         # transform=transformation
#     ) 

# full_dataset_v2 = []   
# for i in range(len(full_dataset)): 
#     full_dataset_v2.append((resize_image(full_dataset[i][0]) , i)) 

# print(full_dataset_v2)


# print(full_dataset[0][1])
# for i in range(len(full_dataset)): 
#         full_dataset[i] = (resize_image(full_dataset[i][0]) , 0) 
        # full_dataset[i][0] = resize_image(full_dataset[i][0])
        # full_dataset[i][1] = correct_label(correct_manga_id) 

# Defining the Model 

In [7]:
# Create a neural net class
class Net(nn.Module):
    
    
    # Defining the Constructor
    def __init__(self, num_classes=3):
        super(Net, self).__init__()
        
        # In the init function, we define each layer we will use in our model
        
        # Our images are RGB, so we have input channels = 3. 
        # We will apply 12 filters in the first convolutional layer
        self.conv1 = nn.Conv2d(in_channels=3, out_channels=12, kernel_size=3, stride=1, padding=1)
        
        # A second convolutional layer takes 12 input channels, and generates 24 outputs
        self.conv2 = nn.Conv2d(in_channels=12, out_channels=12, kernel_size=3, stride=1, padding=1)

        self.conv3 = nn.Conv2d(in_channels=12, out_channels=24, kernel_size=3, stride=1, padding=1)
        
        # We in the end apply max pooling with a kernel size of 2
        self.pool = nn.MaxPool2d(kernel_size=2)
        
        # A drop layer deletes 20% of the features to help prevent overfitting
        self.drop = nn.Dropout2d(p=0.2)
        
        # Our 128x128 image tensors will be pooled twice with a kernel size of 2. 128/2/2 is 32.
        # This means that our feature tensors are now 128 x 128, and we've generated 24 of them
        
        # We need to flatten these in order to feed them to a fully-connected layer
        self.fc = nn.Linear(in_features=24 * 16 * 16, out_features=1)

#         self.fc1= nn.Linear(in_features=10, out_features=1)


    def forward(self, x):
        x=x+1
        
        # In the forward function, pass the data through the layers we defined in the init function
        # print(x)
        # Use a ReLU activation function after layer 1 (convolution 1 and pool)
        x=self.conv1(x)
        
        x=self.pool(x)
       

        x=F.relu(x)

        
      
 
     
        # Use a ReLU activation function after layer 2
        x = F.relu(self.pool(self.conv2(x))) 

        x = F.relu(self.pool(self.conv3(x)))
        
        
        # Select some features to drop to prevent overfitting (only drop during training)
        x = F.dropout(self.drop(x), training=self.training)
        
        # Flatten
        x = x.view(-1, 24 * 16 * 16)
        # Feed to fully-connected layer to predict class
        x = self.fc(x)
        
        # Return class probabilities via a log_softmax function
        
        
        
        # print(x)
        return x
    
device = "cpu"
if (torch.cuda.is_available()):
    # if GPU available, use cuda (on a cpu, training will take a considerable length of time!)
    device = "cuda"

# Create an instance of the model class and allocate it to the device
model = Net(num_classes=len(SFR)).to('cuda')

print(model)

Net(
  (conv1): Conv2d(3, 12, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv2): Conv2d(12, 12, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv3): Conv2d(12, 24, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (drop): Dropout2d(p=0.2, inplace=False)
  (fc): Linear(in_features=6144, out_features=1, bias=True)
)


# Creating Training Loop/Function

In [8]:
def train(model, device, train_loader, optimizer, epoch):
    # Set the model to training mode
    model.train()
    train_loss = 0
    print("Epoch:", epoch)
    # Process the images in batches
    for batch_idx, (data, target) in enumerate(train_loader):

        target=target.float()
        # print(target.shape)
        target=target.reshape(-1,1)
        # Use the CPU or GPU as appropriate
        # Recall that GPU is optimized for the operations we are dealing with
        data, target = data.to(device), target.to(device)
        
        # Reset the optimizer
        optimizer.zero_grad()
        
        # Push the data forward through the model layers
    
        output = model(data)

        
        # Get the loss
        loss = loss_criteria(output, target)
        if batch_idx==0:
            print(output,target,output-target,loss)
        # Keep a running total
        train_loss += loss.item()
        
        # Backpropagate
        loss.backward()
        optimizer.step()

       
        
        # Print metrics so we see some progress
        # print('\tTraining batch {} Loss: {:.6f}'.format(batch_idx + 1, loss.item()))
            
    # return average loss for the epoch
    avg_loss = train_loss / (batch_idx+1)
    print('Training set: Average loss: {:.6f}'.format(avg_loss))
    return avg_loss

# Create Test Function

In [9]:
def test(model, device, test_loader):
    # Switch the model to evaluation mode (so we don't backpropagate or drop)
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        batch_count = 0
        for data, target in test_loader:
            target=target.float()
            target=target.reshape(-1,1)
            batch_count += 1
            data, target = data.to(device), target.to(device)
            
            # Get the predicted classes for this batch
            output = model(data)
            
            # Calculate the loss for this batch
            test_loss += loss_criteria(output, target).item()
            
            # Calculate the accuracy for this batch
            _, predicted = torch.max(output.data, 1)
            correct += torch.sum(target==predicted).item()

    # Calculate the average loss and total accuracy for this epoch
    avg_loss = test_loss / batch_count
    print('Validation set: Average loss: {:.6f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        avg_loss, correct, len(test_loader.dataset),
        100. * correct / len(test_loader.dataset)))
    
    # return average loss for the epoch
    return avg_loss

# Training the Model

In [10]:
# Use an "Adam" optimizer to adjust weights
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Specify the loss criteria
loss_criteria = nn.MSELoss(reduction='sum')

# Track metrics in these arrays
epoch_nums = []
training_loss = []
validation_loss = []


# Train over 10 epochs (We restrict to 10 for time issues)
epochs = 1000
print('Training on', device)
for epoch in range(1, epochs + 1):
        print(epoch)
        train_loss = train(model, device, train_loader, optimizer, epoch)
        test_loss = test(model, device, test_loader)
        epoch_nums.append(epoch)
        training_loss.append(train_loss)
        validation_loss.append(test_loss)
torch.save(model.state_dict(),'/home/juanp/Documents/SURP-2021/Models/Model 9 (3 Layer Regression)/Unique_Loaders')

Training on cuda
1
Epoch: 1
tensor([[ 0.0213],
        [ 0.1842],
        [ 0.0538],
        [-0.0150],
        [ 0.1044],
        [ 0.0814],
        [ 0.1706],
        [ 0.0490],
        [-0.1317],
        [ 0.1957],
        [ 0.0825],
        [-0.1015],
        [ 0.0575],
        [-0.0808],
        [ 0.0151],
        [ 0.0305],
        [ 0.2024],
        [ 0.0796],
        [ 0.0694],
        [ 0.1068],
        [-0.0089],
        [ 0.1945],
        [ 0.0181],
        [-0.1000],
        [-0.0804],
        [ 0.1582],
        [ 0.0294],
        [ 0.0476],
        [ 0.0351],
        [-0.0529],
        [-0.0031],
        [ 0.0136],
        [-0.0322],
        [ 0.0043],
        [-0.1196],
        [-0.0405],
        [ 0.0954],
        [ 0.0305],
        [ 0.0642],
        [ 0.0190],
        [ 0.0593],
        [-0.0621],
        [ 0.0080],
        [ 0.2171],
        [-0.0064],
        [ 0.0585],
        [ 0.1302],
        [ 0.0496],
        [-0.0274],
        [ 0.0891]], device='cuda:0', grad

Training set: Average loss: 88.326747
Validation set: Average loss: 11.614406, Accuracy: 0/11844 (0%)

4
Epoch: 4
tensor([[10.5883],
        [ 9.9286],
        [10.9124],
        [ 9.6288],
        [10.5563],
        [ 7.7772],
        [ 8.3562],
        [12.4294],
        [ 8.4451],
        [10.6468],
        [ 8.0888],
        [ 8.1896],
        [11.5775],
        [ 9.8881],
        [10.7160],
        [10.7545],
        [10.8239],
        [ 9.7230],
        [11.1398],
        [ 8.6731],
        [11.7822],
        [ 6.3450],
        [10.6059],
        [10.5971],
        [10.8840],
        [ 9.6464],
        [ 8.9249],
        [11.6550],
        [10.2854],
        [11.6583],
        [10.3120],
        [ 9.2027],
        [10.0603],
        [ 9.8185],
        [ 9.4683],
        [10.1614],
        [ 8.7144],
        [10.2656],
        [ 9.8618],
        [ 6.1369],
        [ 9.4709],
        [ 9.4242],
        [ 9.6368],
        [ 8.4375],
        [ 8.7656],
        [10.1579],
        [11.

Training set: Average loss: 74.887714
Validation set: Average loss: 10.352535, Accuracy: 0/11844 (0%)

7
Epoch: 7
tensor([[10.6398],
        [10.5624],
        [10.0748],
        [10.8183],
        [10.6687],
        [10.1436],
        [10.3187],
        [ 9.9275],
        [ 9.2094],
        [ 9.3600],
        [ 9.4592],
        [ 9.2792],
        [10.5466],
        [12.5365],
        [12.7758],
        [ 9.8454],
        [ 9.5191],
        [ 9.7143],
        [ 9.9244],
        [ 9.7856],
        [10.9135],
        [11.7608],
        [10.5991],
        [10.2412],
        [11.3299],
        [11.4252],
        [ 9.7815],
        [10.6008],
        [10.6112],
        [10.0469],
        [ 8.6725],
        [ 8.0357],
        [ 8.6953],
        [10.9213],
        [10.7146],
        [10.4744],
        [12.4622],
        [ 9.8461],
        [ 9.3479],
        [12.1842],
        [10.1199],
        [ 8.9840],
        [ 9.1980],
        [10.8194],
        [ 8.7463],
        [10.1114],
        [ 9.

Training set: Average loss: 67.999908
Validation set: Average loss: 9.203256, Accuracy: 0/11844 (0%)

10
Epoch: 10
tensor([[10.0158],
        [ 8.0758],
        [10.8193],
        [ 9.3279],
        [ 9.9671],
        [10.1220],
        [ 8.1485],
        [ 9.3265],
        [10.8362],
        [10.0672],
        [ 9.3533],
        [11.2834],
        [10.3905],
        [10.6933],
        [ 8.5585],
        [11.7108],
        [12.3514],
        [10.8612],
        [11.5978],
        [11.6894],
        [10.9522],
        [10.0038],
        [10.7898],
        [ 9.4406],
        [11.2887],
        [10.7556],
        [10.8957],
        [10.4267],
        [10.5114],
        [10.8167],
        [ 8.0340],
        [10.6566],
        [ 9.0181],
        [11.0150],
        [ 9.5610],
        [10.0480],
        [10.0020],
        [ 8.6556],
        [11.9604],
        [ 9.2964],
        [ 8.6151],
        [ 9.7760],
        [10.3251],
        [10.8450],
        [ 8.9156],
        [ 9.5850],
        [ 9

Training set: Average loss: 61.348603
Validation set: Average loss: 7.500498, Accuracy: 0/11844 (0%)

13
Epoch: 13
tensor([[10.1032],
        [ 8.6488],
        [ 8.6989],
        [ 8.5644],
        [ 9.3292],
        [ 9.7657],
        [ 8.7902],
        [ 7.8306],
        [ 9.7914],
        [ 9.8126],
        [10.5075],
        [ 9.9911],
        [ 9.3544],
        [ 9.8526],
        [ 8.1257],
        [ 9.0742],
        [10.1285],
        [ 9.1131],
        [ 8.8120],
        [ 9.8304],
        [10.1950],
        [ 8.7730],
        [ 9.0611],
        [10.5059],
        [12.0077],
        [10.4118],
        [10.3045],
        [ 9.9276],
        [11.1004],
        [ 9.1682],
        [10.6480],
        [ 7.4769],
        [10.1818],
        [10.3452],
        [ 8.6148],
        [ 9.5556],
        [10.6328],
        [ 8.8991],
        [10.5430],
        [11.4380],
        [ 7.9456],
        [ 8.9483],
        [ 8.2735],
        [ 9.6677],
        [10.5428],
        [11.2182],
        [10

...

Training set: Average loss: 4.745337
Validation set: Average loss: 5.617778, Accuracy: 0/11844 (0%)

988
Epoch: 988
tensor([[ 9.5452],
        [ 9.4010],
        [ 9.6002],
        [ 9.2150],
        [ 9.7071],
        [ 9.3576],
        [ 9.5688],
        [ 9.4012],
        [ 9.2948],
        [ 9.7031],
        [ 9.0949],
        [ 9.7354],
        [ 9.6358],
        [ 9.5435],
        [ 9.6363],
        [ 9.6016],
        [ 9.5318],
        [ 9.8232],
        [ 9.6638],
        [ 9.4810],
        [ 9.7153],
        [ 9.5502],
        [10.4296],
        [10.1066],
        [10.2573],
        [10.6673],
        [ 9.9387],
        [10.5499],
        [ 9.9323],
        [ 9.8053],
        [10.0510],
        [10.1024],
        [ 9.9683],
        [ 9.8690],
        [ 9.9221],
        [10.0783],
        [10.0272],
        [ 9.8588],
        [ 9.9470],
        [ 9.8015],
        [ 9.8805],
        [ 9.5304],
        [ 9.7296],
        [ 9.7604],
        [ 9.3678],
        [ 9.3254],
        [ 

Training set: Average loss: 4.883396
Validation set: Average loss: 5.791028, Accuracy: 0/11844 (0%)

991
Epoch: 991
tensor([[ 9.3461],
        [ 9.5701],
        [ 9.7562],
        [ 9.3815],
        [ 9.6084],
        [ 9.4757],
        [ 9.6491],
        [ 9.5903],
        [ 9.4299],
        [ 9.4545],
        [ 9.5085],
        [ 9.8391],
        [ 9.8071],
        [ 9.6887],
        [ 9.5443],
        [ 9.6787],
        [ 9.8867],
        [ 9.4287],
        [ 9.5303],
        [ 9.6243],
        [ 9.6461],
        [ 9.4020],
        [ 9.9620],
        [10.2158],
        [10.0574],
        [10.6827],
        [10.2812],
        [10.1256],
        [10.1032],
        [10.2034],
        [ 9.8591],
        [10.0816],
        [10.5727],
        [ 9.7265],
        [ 9.9950],
        [ 9.8001],
        [ 9.7600],
        [ 9.7972],
        [ 9.9397],
        [ 9.6584],
        [ 9.7592],
        [ 9.6897],
        [ 9.6344],
        [ 9.8245],
        [ 9.8172],
        [ 9.4562],
        [ 

Training set: Average loss: 4.918158
Validation set: Average loss: 5.640497, Accuracy: 0/11844 (0%)

994
Epoch: 994
tensor([[ 9.4196],
        [ 9.2951],
        [ 9.2980],
        [ 9.4496],
        [ 9.6799],
        [ 9.3114],
        [ 9.2758],
        [ 9.2060],
        [ 9.4704],
        [ 9.4111],
        [ 9.5836],
        [ 9.9422],
        [ 9.7905],
        [ 9.6416],
        [ 9.6828],
        [ 9.5487],
        [ 9.8604],
        [ 9.7598],
        [ 9.6334],
        [ 9.5628],
        [ 9.8805],
        [ 9.7755],
        [10.0896],
        [10.1263],
        [10.2723],
        [ 9.5175],
        [ 9.8382],
        [10.0424],
        [ 9.9171],
        [10.2118],
        [10.4640],
        [ 9.8269],
        [ 9.8989],
        [ 9.8792],
        [ 9.9071],
        [ 9.9982],
        [ 9.9915],
        [ 9.7755],
        [10.0579],
        [ 9.8840],
        [ 9.8784],
        [ 9.8474],
        [ 9.7625],
        [ 9.7489],
        [ 9.3559],
        [ 9.4526],
        [ 

Training set: Average loss: 4.859211
Validation set: Average loss: 5.691691, Accuracy: 0/11844 (0%)

997
Epoch: 997
tensor([[ 9.6899],
        [ 9.4833],
        [ 9.4465],
        [ 9.1804],
        [ 9.5323],
        [ 9.2401],
        [ 9.5554],
        [ 9.5973],
        [ 9.4633],
        [ 9.2557],
        [ 9.4982],
        [ 9.4955],
        [ 9.7600],
        [ 9.4553],
        [ 9.5905],
        [ 9.3831],
        [ 9.4431],
        [ 9.6277],
        [ 9.6779],
        [ 9.6319],
        [ 9.6742],
        [ 9.5023],
        [10.0494],
        [10.1122],
        [ 9.7484],
        [10.1538],
        [10.2135],
        [ 9.9731],
        [ 9.9802],
        [10.1814],
        [10.4758],
        [10.4833],
        [10.3013],
        [ 9.7734],
        [ 9.9507],
        [ 9.8805],
        [10.1525],
        [ 9.8223],
        [ 9.7592],
        [ 9.9047],
        [ 9.9291],
        [ 9.8434],
        [ 9.8489],
        [ 9.8559],
        [ 9.5116],
        [ 9.5653],
        [ 

Training set: Average loss: 4.777771
Validation set: Average loss: 5.891528, Accuracy: 0/11844 (0%)

1000
Epoch: 1000
tensor([[ 9.3282],
        [ 9.6797],
        [ 9.3099],
        [ 9.4433],
        [ 9.7758],
        [ 9.3837],
        [ 9.3401],
        [ 9.5047],
        [ 9.5549],
        [ 9.5541],
        [ 9.3515],
        [ 9.8620],
        [ 9.8451],
        [ 9.6916],
        [ 9.6820],
        [ 9.6101],
        [ 9.5950],
        [ 9.5544],
        [ 9.9506],
        [ 9.8773],
        [ 9.5463],
        [ 9.6888],
        [10.1935],
        [10.0161],
        [10.1519],
        [ 9.9466],
        [10.2595],
        [ 9.8206],
        [ 9.8531],
        [10.0098],
        [10.1162],
        [10.0555],
        [ 9.8051],
        [ 9.9686],
        [ 9.8719],
        [ 9.8478],
        [ 9.9770],
        [ 9.8722],
        [ 9.8272],
        [ 9.8695],
        [ 9.8052],
        [ 9.6932],
        [ 9.8962],
        [ 9.8969],
        [ 9.0458],
        [ 9.2913],
        

In [12]:
%matplotlib qt

plt.figure(figsize=(15,15))
plt.plot(epoch_nums, np.log10(training_loss))
plt.plot(epoch_nums, np.log10(validation_loss))
plt.xlabel('epoch')
plt.ylabel('Log of loss')
plt.legend(['training', 'validation'], loc='upper right')
plt.show()
plt.savefig('Unique_Epoch_Loss')
